In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
import seaborn as sns
import plotly.graph_objects as go
import scipy.stats as st
import plotly.express as px
import json
import unidecode

In [2]:
data_bac = pd.read_csv("../data/CleanData/data_bac.csv")
data_bac 

C:\Users\Alexandra\AppData\Local\Temp\ipykernel_20340\2288450706.py:1: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  data_bac = pd.read_csv("../data/CleanData/data_bac.csv")


candidate_unique_code gender                     specialization  \
0                       10387      F                Științe ale Naturii   
1                       11013      M             Matematica-Informatica   
2                      125241      F                          Filologie   
3                       10654      F  Tehnician în activități de comerț   
4                       11067      F                    Științe Sociale   
...                       ...    ...                                ...   
1264051               1647212      M                          Filologie   
1264052               1647215      F                    Științe Sociale   
1264053               1647219      F           Tehnician electrotehnist   
1264054               1647223      F             Învăţător - educatoare   
1264055               1647309      F                          Filologie   

           profile field_of_study form_of_education candidate_environment  \
0             Real      Teoretică                Zi                 URBAN   
1             Real      Teoretică                Zi                 URBAN   
2             Uman      Teoretică  Frecvență redusă                 URBAN   
3         Servicii    Tehnologică                Zi                 RURAL   
4             Uman      Teoretică  Frecvență redusă                 URBAN   
...            ...            ...               ...                   ...   
1264051       Uman      Teoretică                Zi                 RURAL   
1264052       Uman      Teoretică                Zi                 RURAL   
1264053     Tehnic    Tehnologică                Zi                 RURAL   
1264054  Pedagogic    Vocațională                Zi                 URBAN   
1264055       Uman      Teoretică                Zi                 URBAN   

         unit_SIIIR          class_year           subject_ea  ...   oral_pmo  \
0        1561100746    a XII-a RES 2014  Limba română (REAL)  ...         B1   
1        2561102144           a XII-a B  Limba română (REAL)  ...         A2   
2        1661104708          a XIII-a C  Limba română (UMAN)  ...         A1   
3        2761102702           a XII-a D  Limba română (REAL)  ...         A1   
4        3661100016          a XIII-a A  Limba română (UMAN)  ...         B2   
...             ...                 ...                  ...  ...        ...   
1264051  5161103555           a XII-a B  Limba română (UMAN)  ...  Neevaluat   
1264052   461107757           a XII-a D  Limba română (UMAN)  ...  Neevaluat   
1264053  2861100689  a XII-a A electric  Limba română (REAL)  ...  Neevaluat   
1264054  4061205699           a XII-a A  Limba română (UMAN)  ...  Neevaluat   
1264055  4061102341           a XII-a H  Limba română (UMAN)  ...  Neevaluat   

           oral_io digital_score      status average  year session  \
0               B1          38.0  Nepromovat     NaN  2018       1   
1               A2          64.0  Nepromovat    5.80  2018       1   
2               A1          45.0  Nepromovat    5.78  2018       1   
3               A1          75.0  Nepromovat    5.80  2018       1   
4               B2          44.0  Nepromovat     NaN  2018       1   
...            ...           ...         ...     ...   ...     ...   
1264051  Neevaluat          11.0  Nepromovat     NaN  2025       1   
1264052  Neevaluat          38.0    Promovat    7.06  2025       1   
1264053  Neevaluat          31.0      Absent     NaN  2025       1   
1264054  Neevaluat          37.0    Promovat    7.51  2025       1   
1264055  Neevaluat          42.0    Promovat    9.55  2025       1   

        final_score_ea final_score_ec final_score_ed  
0                 6.60           5.25           4.40  
1                 6.30           5.05           6.05  
2                 5.10           5.30           6.95  
3                 6.00           5.40           6.00  
4                 4.60           5.30           5.00  
...                ...            ...            .

In [3]:
#renaming certain columns 
data_bac = data_bac.rename(columns= {'subject_ea': 'core_subject_1','subject_ec': 'core_subject_2', 'subject_ed': 'elective_subject','status_ea': 'status_subject_1', 'status_ec': 'status_subject_2', 'status_ed': 'status_elective_subject', 'final_score_ea': 'final_score_subject_1','final_score_ec': 'final_score_subject_2', 'final_score_ed': 'final_score_elective_subject'})

In [4]:
# translating status column
data_bac['status'] = data_bac['status'].replace({
    'Absent': 'Absent',
    'Eliminat': 'Disqualified',
    'Neevaluat': 'Not Evaluated',
    'Nepromovat': 'Failed',
    'Promovat': 'Passed'
})


In [5]:
# translating status_subject_1 column
data_bac['status_subject_1'] = data_bac['status_subject_1'].replace({
    'Absent': 'Absent',
    'Eliminat': 'Disqualified',
    'Neevaluat': 'Not Evaluated',
    'Nepromovat': 'Failed',
    'Promovat': 'Passed'
})


In [6]:
# translating status_subject_2 column
data_bac['status_subject_2'] = data_bac['status_subject_2'].replace({
    'Absent': 'Absent',
    'Eliminat': 'Disqualified',
    'Neevaluat': 'Not Evaluated',
    'Nepromovat': 'Failed',
    'Promovat': 'Passed'
})

In [7]:
# translating status_elective_subject column
data_bac['status_elective_subject'] = data_bac['status_elective_subject'].replace({
    'Absent': 'Absent',
    'Eliminat': 'Disqualified',
    'Neevaluat': 'Not Evaluated',
    'Nepromovat': 'Failed',
    'Promovat': 'Passed'
})

### Data Exploration

- #### Students' exam performance

In [8]:
#checking how many students passed, failed or were absent per year, based on their final status
status_per_year = (
    data_bac
    .groupby('year')['status']
    .value_counts()
    .unstack(fill_value=0)
    .reset_index()
)

print(status_per_year)


status  year  Absent  Disqualified  Failed  Not Evaluated  Passed
0       2018   21896           229   58497              0   92069
1       2019   15072           151   59071              0   95678
2       2020   15517           420   70939              0  101798
3       2021   13121           223   56070              0   94391
4       2022   10956           216   45366              0   96383
5       2023   10226           136   46913              0   98372
6       2024    9667           150   43460              1  105311
7       2025    3092            64   22999              0   75602


In [9]:
# percentages of students passed, failed or absent per year
percentage_per_year = (
    data_bac
    .groupby('year')['status']
    .value_counts(normalize=True)
    .mul(100)
    .unstack(fill_value=0)
    .round(2)
    .reset_index()
)

percentage_per_year


status  year  Absent  Disqualified  Failed  Not Evaluated  Passed
0       2018   12.68          0.13   33.87            0.0   53.31
1       2019    8.87          0.09   34.75            0.0   56.29
2       2020    8.22          0.22   37.60            0.0   53.95
3       2021    8.01          0.14   34.23            0.0   57.62
4       2022    7.16          0.14   29.67            0.0   63.03
5       2023    6.57          0.09   30.14            0.0   63.20
6       2024    6.10          0.09   27.40            0.0   66.40
7       2025    3.04          0.06   22.60            0.0   74.30

From 2018 to 2025, the distribution of student outcomes shows a clear positive trend in **performance** and **participation**. The proportion of students who passed steadily increased from 53.3% in 2018 to 74.3% in 2025 or 66.4% in 2024, indicating a consistent improvement in overall success rates. Correspondingly, the percentage of students who failed decreased from 33.9% to 22.6% in 2025 or 27.4% in 2024, suggesting that fewer students are struggling with the exams over time.

At the same time, the proportion of students who were absent dropped significantly, from 12.7% in 2018 to just 3.0% in 2025 or, more accurate, 6.1% in 2024, reflecting improved attendance or exam participation. The categories of Disqualified and Not Evaluated remain negligible throughout the period, indicating stable administrative procedures and evaluation consistency.

Overall, the data suggests that educational outcomes are improving steadily. The increase in passed students appears to be mirrored by the reduction in both failed and absent students, pointing to effective interventions, better preparation, or enhanced student engagement. The trends highlight a positive shift in student performance over the eight-year period. We focus more on the year **2024**, as the data for 2025 includes only one registered session. Therefore, the 2025 results may not fully reflect the student outcomes and should be interpreted with caution.

In [10]:
plot_data = percentage_per_year.set_index('year')

fig = go.Figure()


for col in plot_data.columns:
    fig.add_trace(
        go.Scatter(
            x=plot_data.index,
            y=plot_data[col],
            mode='lines+markers+text', 
            name=col,
            text=[f"{v:.1f}%" if v > 0 else "" for v in plot_data[col]],  
            textposition='top center',
            hovertemplate='Year: %{x}<br>Status: %{text}'  
        )
    )

fig.update_layout(
    title='Final Status Percentages per Year',
    xaxis_title='Year',
    yaxis_title='Percentage (%)',
    yaxis=dict(range=[0, 100]),  
    hovermode='x unified'
)

fig.show()


In [11]:
#checking how many students were evaluated for their first exam (status_ea), but were absents for the next ones (status_ec, status_ed) per each year

passing_score = 5

passed_subject_1= data_bac[
    (data_bac['status_subject_1'] == 'Passed') &               
    (data_bac['final_score_subject_1'] >= passing_score) &        
    ((data_bac['status_subject_2'] != 'Passed') |             
     (data_bac['status_subject_2'].isna())) &
    ((data_bac['status_elective_subject'] != 'Passed') |             
     (data_bac['status_elective_subject'].isna()))
]


In [12]:
passed_only_subject_1 = (
    passed_subject_1
    .groupby('year')
    .size()
    .reset_index(name='passed_only_subject_1')
)

print(passed_only_subject_1)


   year  passed_only_subject_1
0  2018                  10732
1  2019                  10190
2  2020                  16308
3  2021                  10036
4  2022                   6230
5  2023                   6656
6  2024                   6241
7  2025                   2651


The analysis of students who were evaluated in their first exam but were absent for subsequent exams reveals that in 2018–2020, a substantial number of students fell into this category, ranging from 10,190 in 2019 to 16,308 in 2020, indicating that a significant portion of students did not continue to take the remaining exams after their first evaluation. The peak in 2020 may reflect disruptions, such as those caused by the COVID-19 pandemic, which affected exam attendance and scheduling.

From 2021 onwards, there is a notable decline in these numbers, dropping to around 6,200–6,600 students in 2022–2024, suggesting improved follow-through and higher student engagement in completing all required exams. The sharp decrease to 2,651 students in 2025 should be interpreted with caution, as it corresponds to only one registered exam session. The data indicates a positive trend in student participation in subsequent exams, reflecting a better attendance.

In [13]:
#checking how many students were evaluated for their first two exams (status_ea, status_ec), but were absents for the last one (status_ed) per each year

not_elective_subject = data_bac[
    (data_bac['status_subject_1'] == 'Passed') &   
    (data_bac['status_subject_2'] == 'Passed') &  
    ((data_bac['status_elective_subject'] != 'Passed') | data_bac['status_elective_subject'].isna()) 
]


In [14]:
not_elective_subject_per_year = (
    not_elective_subject
    .groupby('year')
    .size()
    .reset_index(name='elective_subject_not_passed')
)

print(not_elective_subject_per_year)


   year  elective_subject_not_passed
0  2018                         7684
1  2019                         7015
2  2020                        10413
3  2021                         7691
4  2022                         7020
5  2023                         7850
6  2024                         8434
7  2025                         3466


The analysis of students who were evaluated for their first two exams but were absent for the last one reveals that between 2018 and 2019, approximately 7,000 students fell into this category. In 2020, the number spiked to 10,413 students, likely reflecting external disruptions such as the COVID-19 pandemic, which may have affected student attendance and exam completion.

From 2021 to 2024, the numbers stabilized between 7,000 and 8,400 students, indicating that while most students complete all exams, a small but persistent group does not take the final exam. The slight upward trend in recent years (7,020 in 2022 to 8,434 in 2024) reflects changes in exam scheduling, elective requirements, or student behavior.

The sharp decrease to 3,466 students in 2025 should be interpreted with caution, as this year includes only one registered session and may not fully represent the total student population.

In [15]:
#checking the average grade per year for two compulsory exams in subjects -> columns: 'final_score_subject_1' and 'final_score_subject_2', as well as one exam chosen by the student: 'final_score_elective_subject'
avg_per_year = (
    data_bac
    .groupby('year')[['final_score_subject_1', 'final_score_subject_2', 'final_score_elective_subject']]
    .mean()
    .round(2)
    .reset_index()
)
avg_per_year

year  final_score_subject_1  final_score_subject_2  \
0  2018                   5.99                   5.29   
1  2019                   6.33                   5.60   
2  2020                   6.40                   5.45   
3  2021                   6.40                   5.64   
4  2022                   6.37                   6.29   
5  2023                   6.40                   6.24   
6  2024                   6.72                   6.54   
7  2025                   6.97                   6.95   

   final_score_elective_subject  
0                          6.16  
1                          6.50  
2                          6.32  
3                          6.56  
4                          6.84  
5                          6.70  
6                          6.97  
7                          7.54

In [21]:
import plotly.graph_objects as go

fig = go.Figure()

for col, label in zip(
    ['final_score_subject_1', 'final_score_subject_2', 'final_score_elective_subject'],
    ['subject_1', 'subject_2', 'elective_subject']
):
    fig.add_trace(
        go.Scatter(
            x=avg_per_year['year'],
            y=avg_per_year[col],
            mode='lines+markers',
            name=label
        )
    )

fig.update_layout(
    title='Average Final Scores per Year',
    xaxis_title='Year',
    yaxis_title='Average Final Score',
    hovermode='x unified'
)

fig.show()


The analysis of average grades per year for two compulsory exams and one elective exam shows a steady improvement in student performance over time. For the first compulsory exam, the average grade increased from 5.99 in 2018 to 6.97 in 2025 or 6.72 in 2024, while the second compulsory exam rose from 5.29 to 6.95 in 2025 or 6.54 in 2024. The elective exam, chosen by the students, consistently exhibits slightly higher averages, increasing from 6.16 in 2018 to 7.54 in 2025 or 6.97 in 2024.

The data highlights a positive trajectory in academic achievement, with elective subjects consistently giving students slightly higher scores, and recent years showing particularly strong performance across all subjects.

In [110]:
#checking the percentage of promovability per school 
promovability_status = 'Passed'  
#total students per school per year
total_per_school_year = (
    data_bac
    .groupby(['unit_SIIIR', 'year'])
    .size()
    .reset_index(name='total_students')
)

#promoted students per school per year
promovability_per_school_year = (
    data_bac[data_bac['status'] == promovability_status]
    .groupby(['unit_SIIIR', 'year'])
    .size()
    .reset_index(name='promoted_students')
)

#merge and calculate percentage
promovability_year = total_per_school_year.merge(
    promovability_per_school_year, 
    on=['unit_SIIIR', 'year'], 
    how='left'
)

#fill NaN (schools/years with no promoted students)
promovability_year['promoted_students'] = promovability_year['promoted_students'].fillna(0)

#calculate promovability percentage
promovability_year['promovability_pct'] = (
    promovability_year['promoted_students'] / promovability_year['total_students'] * 100
).round(2)

promovability_year.head(8)



unit_SIIIR  year  total_students  promoted_students  promovability_pct
0   161100022  2018              69                9.0              13.04
1   161100022  2019              49               14.0              28.57
2   161100022  2020             103               22.0              21.36
3   161100022  2021              97               20.0              20.62
4   161100022  2022              77               15.0              19.48
5   161100022  2023              74               21.0              28.38
6   161100022  2024             105               33.0              31.43
7   161100022  2025              63               27.0              42.86

School 161100022 exhibits a clear upward trend despite starting from relatively low values. Promovability rises from 13.04% in 2018 to 42.86% in 2025, with steady growth particularly after 2022. This suggests improving outcomes over time, although the school’s performance remains below that of the higher-performing institutions.

In [111]:
#checking the promovability trend over 2018-2025 for ONLY 5 schools that grew the most
#pivot table 
pivot = promovability_year.pivot(index='year', columns='unit_SIIIR', values='promovability_pct')

# Calculate growth (last year - first year)
growth = pivot.loc[2025] - pivot.loc[2018]

# Select top 5 schools with highest growth
top5_schools = growth.sort_values(ascending=False).head(5).index.tolist()

print("Top 5 schools with highest growth:", top5_schools)


Top 5 schools with highest growth: [1361100731, 3061101347, 3061102529, 3261101819, 2961201646]


In [112]:
top5_data = promovability_year[promovability_year['unit_SIIIR'].isin(top5_schools)]

In [ ]:
#visualizing the evolution of each school
colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd']

fig = go.Figure()

for school, color in zip(top5_data['unit_SIIIR'].unique(), colors):
    school_data = top5_data[top5_data['unit_SIIIR'] == school]

    fig.add_trace(
        go.Scatter(
            x=school_data['year'],
            y=school_data['promovability_pct'],
            mode='lines+markers+text',
            name=str(school),
            line=dict(color=color),
            marker=dict(size=8),
            text=[f"{v:.1f}%" if v > 0 else "" for v in school_data['promovability_pct']],
            textposition='top center',
            hovertemplate=(
                'School: %{name}<br>'
                'Year: %{x}<br>'
                'Promovability: %{y:.1f}%<extra></extra>'
            )
        )
    )

fig.update_layout(
    title='Promovability Trend (2018-2025) for Top 5 Growing Schools',
    xaxis_title='Year',
    yaxis_title='Promovability (%)',
    yaxis=dict(range=[0, 100]),
    legend_title='School Code (unit_SIIIR)',
    hovermode='x unified',
    template='plotly_white'
)

fig.show()


In [114]:
#student pass rate per county
#loading the data
list_schools = pd.read_csv('../data/CleanData/list_schools.csv')


In [115]:
#merging the two dataframes on unit_SIIIR
data_loc = data_bac.merge(list_schools[['unit_SIIIR','county']], on='unit_SIIIR', how='left')
data_loc.shape

(1264056, 35)

In [127]:
#grouping by year and county
county_pass = (
    data_loc.groupby(['year', 'county'])
    .agg(
        total_students=('candidate_unique_code', 'count'),
        passed_students=('status', lambda x: (x == 'Passed').sum())
    )
    .reset_index()
)

#calculate percentage
county_pass['promovability_pct'] = (county_pass['passed_students'] / county_pass['total_students']) * 100
# Round the percentage to 2 decimals
county_pass['promovability_pct'] = county_pass['promovability_pct'].round(2)



In [128]:
#choosing the years
years_to_plot = [2018, 2020, 2022, 2024]
county_pass = county_pass[county_pass['year'].isin(years_to_plot)]


In [ ]:
#normalizing your DataFrame county names
county_pass['county_name'] = county_pass['county'].apply(lambda x: unidecode(x.strip().lower()))

#normalizing GeoJSON names
for feature in romania_geojson['features']:
    feature['properties']['name_clean'] = unidecode(feature['properties']['name'].strip().lower())


In [141]:
#filtering only the years you want
years_to_plot = [2018, 2020, 2022, 2024]
df = county_pass[county_pass['year'].isin(years_to_plot)]

#creating choropleth with animation
fig = px.choropleth(
    df,
    geojson=romania_geojson,
    locations='county_name',           
    featureidkey='properties.name_clean', 
    color='promovability_pct',
    animation_frame='year',            
    color_continuous_scale='Blues',
    range_color=(0, 100),
    labels={'promovability_pct':'Promovability (%)'},
    title='Student Pass Rate per County (2018-2024)'
)

fig.update_geos(fitbounds="locations", visible=False)
fig.show()


In [23]:
#checking if the environment has an influence on student's performance

stats_env = (
    data_bac
    .groupby(['year','candidate_environment'])[['final_score_subject_1', 'final_score_subject_2', 'final_score_elective_subject']]
    .agg(['mean', 'median'])
    .round(2)
)

stats_env
 

final_score_subject_1        final_score_subject_2  \
                                            mean median                  mean   
year candidate_environment                                                      
2018 RURAL                                  5.41   5.80                  4.48   
     URBAN                                  6.28   6.55                  5.69   
2019 RURAL                                  5.83   6.00                  4.84   
     URBAN                                  6.59   6.65                  5.99   
2020 RURAL                                  5.96   6.00                  4.76   
     URBAN                                  6.64   6.70                  5.83   
2021 RURAL                                  5.95   6.10                  5.03   
     URBAN                                  6.64   6.85                  5.97   
2022 RURAL                                  5.92   6.00                  5.67   
     URBAN                                  6.63   6.65                  6.64   
2023 RURAL                                  6.02   6.05                  5.67   
     URBAN                                  6.62   6.80                  6.56   
2024 RURAL                                  6.28   6.30                  5.96   
     URBAN                                  6.99   7.30                  6.89   
2025 RURAL                                  6.53   6.55                  6.31   
     URBAN                                  7.23   7.60                  7.32   

                                  final_score_elective_subject         
                           median                         mean median  
year candidate_environment                                             
2018 RURAL                   5.10                         5.53   6.40  
     URBAN                   6.05                         6.47   7.35  
2019 RURAL                   5.20                         5.96   6.60  
     URBAN                   6.15                         6.78   7.50  
2020 RURAL                   5.15                         5.80   6.40  
     URBAN                   6.10                         6.60   7.35  
2021 RURAL                   5.30                         6.03   6.65  
     URBAN                   6.15                         6.85   7.60  
2022 RURAL                   5.85                         6.37   7.00  
     URBAN                   7.05                         7.11   7.85  
2023 RURAL                   5.95                         6.26   6.85  
     URBAN                   6.95                         6.96   7.65  
2024 RURAL                   6.20                         6.47   7.10  
     URBAN                   7.40                         7.28   8.05  
2025 RURAL                   6.55                         7.05   7.70  
     URBAN                   7.80                         7.82   8.55

As can be seen at a glance, there is a difference between the grades of students from urban environments and those of students from rural environments. Below, we provide a detailed analysis of the hypothesis that students from urban environments achieve higher grades than those from rural environments.

In [24]:
avg_per_year_env = (
    data_bac.groupby(['year', 'candidate_environment'], as_index=False)
      .agg(avg_score=('average', 'mean'))
)


In [27]:
import plotly.graph_objects as go

fig = go.Figure()

for env in avg_per_year_env['candidate_environment'].unique():
    env_data = avg_per_year_env[avg_per_year_env['candidate_environment'] == env]

    fig.add_trace(
        go.Scatter(
            x=env_data['year'],
            y=env_data['avg_score'],
            mode='lines+markers',
            name=env,
            hovertemplate=(
                'Year: %{x}<br>'
                f'Environment: {env}<br>'
                'Average score: %{y:.2f}<extra></extra>'
            )
        )
    )

fig.update_layout(
    title='Average Exam Score per Year by Environment',
    xaxis_title='Year',
    yaxis_title='Average Score',
    hovermode='x unified',
    template='plotly_white'
)

fig.show()


##### Hypothese Testing 1

H0: students from the urban area are not having better grades than students from the rural area

H1: students from the urban area have better grades than others



In [145]:
#checking the content of the column 'candidate_environment'
data_bac['candidate_environment'].unique()

array(['URBAN', 'RURAL'], dtype=object)

In [146]:
#preparing the data
urban = data_bac[data_bac['candidate_environment'] == 'URBAN']['average'].dropna()
non_urban = data_bac[data_bac['candidate_environment'] != 'URBAN']['average'].dropna()


In [147]:
from scipy.stats import ttest_ind

t_stat, p_value = ttest_ind(
    urban,
    non_urban,
    equal_var=False,
    alternative='greater' 
)

print(f"T-statistic: {t_stat:.3f}")
print(f"P-value: {p_value:.4f}")


T-statistic: 113.534
P-value: 0.0000


Students in urban environments have significantly higher average grades than those in non-urban environments, therefore we reject H0.

In [148]:

mean_diff = urban.mean() - non_urban.mean()
pooled_std = np.sqrt((urban.var() + non_urban.var()) / 2)
cohens_d = mean_diff / pooled_std

print(f"Cohen's d: {cohens_d:.2f}")


Cohen's d: 0.27


Statistically, urban students do have higher average grades, but the practical difference is modest.

##### Hypothese Testing 2

H0: Students in urban environments do not have higher scores (subject 1 and 2) than non-urban students.

H1: Students in urban environments have higher scores (subject 1 and 2) than non-urban students.

In [149]:
urban_subj1 = data_bac[data_bac['candidate_environment'] == 'URBAN']['final_score_subject_1'].dropna()
non_urban_subj1 = data_bac[data_bac['candidate_environment'] != 'URBAN']['final_score_subject_1'].dropna()

urban_subj2 = data_bac[data_bac['candidate_environment'] == 'URBAN']['final_score_subject_2'].dropna()
non_urban_subj2 = data_bac[data_bac['candidate_environment'] != 'URBAN']['final_score_subject_2'].dropna()


In [150]:

# subject 1
t1, p1 = ttest_ind(urban_subj1, non_urban_subj1, equal_var=False, alternative='greater')

# subject 2
t2, p2 = ttest_ind(urban_subj2, non_urban_subj2, equal_var=False, alternative='greater')

print(f"Subject 1: t = {t1:.3f}, p = {p1:.4f}")
print(f"Subject 2: t = {t2:.3f}, p = {p2:.4f}")


Subject 1: t = 154.229, p = 0.0000
Subject 2: t = 178.591, p = 0.0000


Students in urban environments scored significantly higher than non-urban students in both subjects.

In [151]:

# subject 1
mean_diff1 = urban_subj1.mean() - non_urban_subj1.mean()
pooled_std1 = np.sqrt((urban_subj1.var() + non_urban_subj1.var()) / 2)
cohens_d1 = mean_diff1 / pooled_std1

# subject 2
mean_diff2 = urban_subj2.mean() - non_urban_subj2.mean()
pooled_std2 = np.sqrt((urban_subj2.var() + non_urban_subj2.var()) / 2)
cohens_d2 = mean_diff2 / pooled_std2

print(f"Subject 1 Cohen's d: {cohens_d1:.2f}")
print(f"Subject 2 Cohen's d: {cohens_d2:.2f}")


Subject 1 Cohen's d: 0.29
Subject 2 Cohen's d: 0.33


The differences are statistically significant (due to large sample sizes), but the actual difference in grades is modest in practical terms.

In [28]:
#counting how many girls and boys enrolled in the exam per year
counts_per_year_gender = (
    data_bac.groupby(['year', 'gender'])
      .size()
      .reset_index(name='count')
)
counts_per_year_gender


year gender  count
0   2018      F  87931
1   2018      M  84760
2   2019      F  87130
3   2019      M  82842
4   2020      F  93976
5   2020      M  94698
6   2021      F  83503
7   2021      M  80302
8   2022      F  78923
9   2022      M  73998
10  2023      F  79705
11  2023      M  75942
12  2024      F  81092
13  2024      M  77497
14  2025      F  52846
15  2025      M  48911

In [ ]:
#checking the average score per year by gender

avg_per_year_gender = (
    data_bac.groupby(['year', 'gender'], as_index=False)
      .agg(avg_score=('average', 'mean'))
)

avg_per_year_gender['avg_score'] = avg_per_year_gender['avg_score'].round(2)

avg_per_year_gender

year gender  avg_score
0   2018      F       7.82
1   2018      M       7.30
2   2019      F       7.80
3   2019      M       7.31
4   2020      F       7.93
5   2020      M       7.39
6   2021      F       7.86
7   2021      M       7.37
8   2022      F       6.02
9   2022      M       5.13
10  2023      F       7.81
11  2023      M       7.37
12  2024      F       8.08
13  2024      M       7.62
14  2025      F       8.18
15  2025      M       7.76

In [30]:
#visualizing the average exam score per year by gender

fig = px.line(
    avg_per_year_gender,
    x='year',
    y='avg_score',
    color='gender',
    markers=True,
    title='Average Exam Score per Year by Gender'
)

fig.update_layout(
    xaxis_title='Year',
    yaxis_title='Average Score',
    hovermode='x unified',
    template='plotly_white'
)

fig.show()


The analysis of average scores per year by gender reveals a consistent performance gap between female and male students across the years. In every year from 2018 to 2025, **female students** achieve higher average scores than male students, indicating a persistent gender difference in academic performance.

Between 2018 and 2021, average scores remain relatively stable, with female students scoring around 7.8–7.9, while male students score approximately 7.3–7.4. In 2022, a notable drop is observed for both genders, particularly among male students (from 7.37 in 2021 to 5.13 in 2022), suggesting a year-specific disruption that affected overall performance. Despite this decline, female students continue to outperform male students by a substantial margin.

From 2023 onwards, average scores recover and increase steadily for both genders. The performance gap remains relatively stable over time, typically ranging between 0.4 and 0.6 points, which suggests a systematic difference rather than isolated fluctuations.

- #### Students' preferences

In [155]:
#checking the most common preferences of students regarding 'elective_subject', top 3
#consider only students who passed elective_subject
passed_ed = data_bac[data_bac['status_elective_subject'] == 'Passed']  

#count frequency of each elective_subject
subject_counts = passed_ed['elective_subject'].value_counts()

#get top 3 most chosen subjects
top3_subjects = subject_counts.head(3)

print(f"Top 3 most frequently chosen subject_ed subjects among students who passed: {top3_subjects}")


Top 3 most frequently chosen subject_ed subjects among students who passed: elective_subject
Geografie                                                   333523
Anatomie și fiziologie umană, genetică și ecologie umană    210387
Logică, argumentare și comunicare                           160470
Name: count, dtype: int64


Elective subject selection is highly concentrated, with Geography attracting the largest number of students, followed by Anatomy and Human Physiology, Genetics and Human Ecology, and Logic, Argumentation, and Communication. Together, these subjects account for the majority of elective exam choices.

In [156]:
#checking the most common preferences of students regarding 'modern_language', top 3
#consider only students who passed subject_ed
pref_modern_lang = data_bac[['modern_language']]

#count frequency of each subject_ed
subject_counts = pref_modern_lang['modern_language'].value_counts()

#get top 3 most chosen subjects
top3_languages = subject_counts.head(3)

print("Top 3 most frequently chosen modern languages:")
top3_languages


Top 3 most frequently chosen modern languages:


modern_language
Limba engleză            1166405
Limba franceză             84008
Limba germană modernă       7208
Name: count, dtype: int64

The distribution of modern language choices is highly uneven, with English overwhelmingly dominating student preferences. With over 1.16 million students, English is chosen by the vast majority, far surpassing French (84,008 students) and German (7,208 students).

- ### Students' Attendance

In [31]:
#checking how many students are registered to different forms of education
education_counts = (
    data_bac
    .groupby('form_of_education')
    .size()
    .reset_index(name='total_students')
)

education_counts


form_of_education  total_students
0  Frecvență redusă           22124
1             Seral           23706
2                Zi         1218226

In [32]:
#total number of students per year for each form of study
education_per_year = (
    data_bac
    .groupby(['year', 'form_of_education'])
    .size()
    .unstack(fill_value=0)
)

education_per_year


form_of_education  Frecvență redusă  Seral      Zi
year                                              
2018                           3089   3333  166269
2019                           2815   2422  164735
2020                           4645   5044  178985
2021                           3123   3485  157197
2022                           2437   2450  148034
2023                           2681   3213  149753
2024                           2181   2343  154065
2025                           1153   1416   99188

In [33]:
#transforming the results into percentages
education_per_year_pct = education_per_year.div(
    education_per_year.sum(axis=1), axis=0
) * 100

education_per_year_pct.round(2)


form_of_education  Frecvență redusă  Seral     Zi
year                                             
2018                           1.79   1.93  96.28
2019                           1.66   1.42  96.92
2020                           2.46   2.67  94.86
2021                           1.91   2.13  95.97
2022                           1.59   1.60  96.80
2023                           1.72   2.06  96.21
2024                           1.38   1.48  97.15
2025                           1.13   1.39  97.48

In most years, *Seral* attracts a marginally higher share of students than *Frecvență redusă*. This may indicate that evening classes are a more accessible alternative for students who combine education with work or other daytime commitments.

In [34]:
import plotly.graph_objects as go

fig = go.Figure()

# Loop through each column (education type) to create stacked bars
for col in education_per_year_pct.columns:
    fig.add_trace(
        go.Bar(
            x=education_per_year_pct.index,  # years
            y=education_per_year_pct[col],
            name=col,
            text=[f'{v:.2f}%' for v in education_per_year_pct[col]],  # show percentages
            textposition='inside'  # display text inside bars
        )
    )

fig.update_layout(
    title='Percentage of Students per Education Type by Year',
    xaxis_title='Year',
    yaxis_title='Percentage of Students (%)',
    barmode='stack',  # stacked bars
    template='plotly_white'
)

fig.show()


In [160]:
data_bac.columns

Index(['candidate_unique_code', 'gender', 'specialization', 'profile',
       'field_of_study', 'form_of_education', 'candidate_environment',
       'unit_SIIIR', 'class_year', 'core_subject_1', 'modern_language',
       'core_subject_2', 'elective_subject', 'graduation_year', 'status_a',
       'status_b', 'status_c', 'status_d', 'status_subject_1',
       'status_subject_2', 'status_elective_subject', 'ita', 'written_itc',
       'written_pms', 'oral_pmo', 'oral_io', 'digital_score', 'status',
       'average', 'year', 'session', 'final_score_subject_1',
       'final_score_subject_2', 'final_score_elective_subject'],
      dtype='object')

In [161]:
list_schools.columns

Index(['unit_SIIIR', 'unit_name', 'locality', 'county'], dtype='object')